# app

> Gradio app.py

In [ ]:
#| default_exp app

In [ ]:
#| hide
from nbdev.showdoc import *

In [ ]:
# | export
import copy
import os
import gradio as gr
import constants
from lv_recipe_chatbot.vegan_recipe_assistant import (
    SYSTEM_PROMPT,
    vegan_recipe_edamam_search,
    VEGAN_RECIPE_SEARCH_TOOL_SCHEMA,
)
from openai import OpenAI, AssistantEventHandler
from typing_extensions import override
import json

In [ ]:
#| hide
import time
from dotenv import load_dotenv

In [ ]:
#: eval: false
load_dotenv()

True

Need an even handler to send the streaming output to the Gradio app  
[GPT4 streaming output example on hugging face 🤗](https://huggingface.co/spaces/ysharma/ChatGPT4/blob/main/app.pyhttps://huggingface.co/spaces/ysharma/ChatGPT4/blob/main/app.py)  
[Gradio lite let's you insert Gradio app in browser JS](https://www.gradio.app/guides/gradio-litehttps://www.gradio.app/guides/gradio-lite)  
[Streaming output](https://www.gradio.app/main/guides/streaming-outputshttps://www.gradio.app/main/guides/streaming-outputs)

In [ ]:
class EventHandler(AssistantEventHandler):
    def __init__(self, handle_text_delta):
        self.handle_text_delta = handle_text_delta

    @override
    def on_text_delta(self, delta, snapshot):
        self.handle_text_delta(delta.value)

    @override
    def on_event(self, event):
        # Retrieve events that are denoted with 'requires_action'
        # since these will have our tool_calls
        if event.event == "thread.run.requires_action":
            run_id = event.data.id  # Retrieve the run ID from the event data
            self.handle_requires_action(event.data, run_id)

    def handle_requires_action(self, data, run_id):
        tool_outputs = []
        for tool_call in data.required_action.submit_tool_outputs.tool_calls:
            if tool_call.function.name == "vegan_recipe_edamam_search":
                fn_args = json.loads(tool_call.function.arguments)
                data = vegan_recipe_edamam_search(
                    query=fn_args.get("query"),
                )
                tool_outputs.append({"tool_call_id": tool_call.id, "output": data})

        self.submit_tool_outputs(tool_outputs, run_id)

    def submit_tool_outputs(self, tool_outputs, run_id):
        with client.beta.threads.runs.submit_tool_outputs_stream(
            thread_id=self.current_run.thread_id,
            run_id=self.current_run.id,
            tool_outputs=tool_outputs,
            event_handler=EventHandler(),
        ) as stream:
            for text in stream.until_:
                pass

In [ ]:
client = OpenAI()
assistant = client.beta.assistants.create(
    name="Vegan Recipe Finder",
    instructions=SYSTEM_PROMPT
    + "\nChoose the best single matching recipe to the user's query out of the vegan recipe search returned recipes",
    model="gpt-4o",
    tools=[VEGAN_RECIPE_SEARCH_TOOL_SCHEMA],
)

In [ ]:
def run_conversation() -> str:
    run = client.beta.threads.runs.create_and_poll(
        thread_id=thread.id,
        assistant_id=assistant.id,
    )
    while True:
        tool_outputs = []
        tool_calls = (
            []
            if not run.required_action
            else run.required_action.submit_tool_outputs.tool_calls
        )

        for tool_call in tool_calls:
            if tool_call.function.name == "vegan_recipe_edamam_search":
                fn_args = json.loads(tool_call.function.arguments)
                data = vegan_recipe_edamam_search(
                    query=fn_args.get("query"),
                )
                tool_outputs.append({"tool_call_id": tool_call.id, "output": data})

        if tool_outputs:
            try:
                run = client.beta.threads.runs.submit_tool_outputs_and_poll(
                    thread_id=thread.id,
                    run_id=run.id,
                    tool_outputs=tool_outputs,
                )
                print("Tool outputs submitted successfully.")

            except Exception as e:
                print("Failed to submit tool outputs:", e)
                return "Sorry failed to run tools. Try again with a different query."

        if run.status == "completed":
            messages = client.beta.threads.messages.list(thread_id=thread.id)
            data = messages.data
            content = data[0].content
            return content[0].text.value
        time.sleep(0.05)

In [ ]:
# https://www.gradio.app/main/guides/creating-a-chatbot-fast#customizing-your-chatbot


# on chatbot start/ first msg after clear
thread = client.beta.threads.create()


def predict(message, history):
    # if msg no new file handle it as such
    # note that history is a flat list of text messages
    txt = message["text"]
    if txt:
        client.beta.threads.messages.create(
            thread_id=thread.id,
            role="user",
            content=txt,
        )
    files = message["files"]
    # files is only from the last message rather than all historically submitted files
    if files:
        # files[-1].split(".")[-1] in ["jpg", "png", "jpeg", "webp"]:
        file = message["files"][-1]
        file = client.files.create(
            file=open(
                file,
                "rb",
            ),
            purpose="vision",
        )
        client.beta.threads.messages.create(
            thread_id=thread.id,
            content=[
                {
                    "type": "text",
                    "text": "What vegan ingredients do you see in this image?",
                },
                {"type": "image_file", "image_file": {"file_id": file.id}},
            ],
            role="user",
        )
    return run_conversation()


# print(predict({"text": "yo", "files": []}, []))
# print(predict({"text": "suggest a tofu and greens recipe please", "files": []}, []))
# print(predict({"text": "burger", "files": []}, []))
if "demo" in globals():
    demo.close()

demo = gr.ChatInterface(fn=predict, multimodal=True)
demo.launch()

Closing server running on port: 7860
Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.


Tool outputs submitted successfully.
Tool outputs submitted successfully.
Tool outputs submitted successfully.
Tool outputs submitted successfully.
Tool outputs submitted successfully.
Tool outputs submitted successfully.


In [ ]:
def create_demo():
    # sample_images = []
    # all_imgs = [f"{SAMPLE_IMG_DIR}/{img}" for img in os.listdir(SAMPLE_IMG_DIR)]
    # for i, img in enumerate(all_imgs):
    #     if i in [
    #         1,
    #         2,
    #         3,
    #     ]:
    #         sample_images.append(img)
    with gr.ChatInterface() as demo:
        # gr_img = gr.Image(type="filepath")
        # btn = gr.Button(value="Submit image")
        # ingredients_msg = gr.Text(label="Ingredients from image")
        # btn.click(bot.run_img, inputs=[gr_img], outputs=[ingredients_msg])
        # gr.Examples(
        #     examples=sample_images,
        #     inputs=gr_img,
        # )

        chatbot = gr.Chatbot(value=[(None,)])

        msg = gr.Textbox()
        gr.Markdown(
            """**🔃Refresh the page to start from scratch🔃**  
        
        Recipe search tool powered by the [Edamam API](https://www.edamam.com/)  
        
        ![Edamam Logo](https://www.edamam.com/assets/img/small-logo.png)"""
        )
        msg.submit(
            fn=bot.respond, inputs=[msg, chatbot], outputs=[msg, chatbot], queue=False
        )
        # clear.click(lambda: None, None, chatbot, queue=False).then(bot.reset)
        return demo

skip


In [ ]:
#| hide
import nbdev

nbdev.nbdev_export()